# Data Quality

In [1]:
import pandas as pd
from itertools import product
import difflib


### Consistency

In [2]:
df_game_stats = pd.read_excel('datasets_cleaned/game_stats.xlsx')
df_game_stats

position  win_rate  pick_rate  ban_rate  pbi  games_played     grade  \
0            1     50.20      10.21     19.44    3       1737071  0.888667   
1            2     51.50       5.32     15.35    9        905128  1.111000   
2            3     52.42       5.85      6.50   15        995476  1.222000   
3            4     51.00       4.89      7.75    5        832573  1.222000   
4            5     52.14       8.33      6.26   19       1417037  1.333333   
...        ...       ...        ...       ...  ...           ...       ...   
3651       100     40.67       2.45      0.99   -9         19551  4.777667   
3652       101     33.85       0.15      0.71   -2          1158  4.833000   
3653       102     36.99       0.43      0.79   -3          3393  5.000000   
3654       103     30.41       0.24      5.58   -4          1930  5.000000   
3655       104     23.92       0.11      0.93   -2           899  5.166500   

      lane_ID  ranking_ID  champion_ID  
0           1           0           24  
1           1           0          420  
2           1           0           75  
3           1           0          114  
4           1           0           86  
...       ...         ...          ...  
3651        5           9          117  
3652        5           9           20  
3653        5           9           34  
3654        5           9           18  
3655        5           9           15  

[3656 rows x 10 columns]

#### Question 1: are Win_rate_weak and win_rate_strong consistent with champion win_rate?

In [3]:
matchup = pd.read_excel('datasets_cleaned/matchup.xlsx')
matchup

lane_ID  ranking_ID     type  winrate  games_played  champion_ID  \
0            1           0  counter    44.01        100862           24   
1            1           0  counter    44.53         50803           24   
2            1           0  counter    44.85         28349           24   
3            1           0  counter    44.86         14508           24   
4            1           0  counter    45.80          5380           24   
...        ...         ...      ...      ...           ...          ...   
30920        5           9   strong    61.82            55           21   
30921        5           9   strong    60.00            35           21   
30922        5           9   strong    59.57            47           21   
30923        5           9   strong    58.06            62           21   
30924        5           9   strong    56.10            41           21   

       champion_vs_ID  
0                  86  
1                 420  
2                  36  
3                  27  
4                 154  
...               ...  
30920              43  
30921              17  
30922             267  
30923             117  
30924              57  

[30925 rows x 7 columns]

In [4]:
#per ogni champion, lane e ranking la diff della media winrate strong e win rate weak, se positive allora consistent
champion_ID_list = list(matchup['champion_ID'].unique())
len(champion_ID_list)

166

In [5]:
num_iterations = 0
num_inconsistent = 0
list_inconsistent_weak = []
list_inconsistent_strong = []
for champion in champion_ID_list:
    print(f'============================{champion}==============================')
    filter_champion = (matchup['champion_ID'] == champion)

    lanes = list(matchup[filter_champion]['lane_ID'].unique())
    rankings = list(matchup[filter_champion]['ranking_ID'].unique())

    for lane, ranking in product(lanes, rankings):
        print(f'{champion} - {lane} - {ranking}')
        is_computable = False
        filter_2 = (matchup['lane_ID'] == lane) & (matchup['ranking_ID'] == ranking)

        subset = matchup[filter_champion & filter_2]
        mean_counter = None
        mean_strong = None

        if len(subset[subset['type'] == 'counter']) > 0:
            print('Counter: ', subset[subset['type'] == 'counter'][['winrate', 'champion_vs_ID', 'games_played']])
            mean_counter = subset[subset['type'] == 'counter']['winrate'].mean()

        if len(subset[subset['type'] == 'strong']) > 0:
            print('Strong: ', subset[subset['type'] == 'strong'][['winrate', 'champion_vs_ID', 'games_played']])
            mean_strong =  subset[subset['type'] == 'strong']['winrate'].mean()

        avg_win_rate = (df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking), 'win_rate'])
        
        if len(avg_win_rate) > 0:
            if len(avg_win_rate) == 1:
                avg_win_rate = float(avg_win_rate.iloc[0])
            else:
                raise ValueError("Qui valori multipli. problema")
        else:
            avg_win_rate = None

        is_consistent_weak = False 
        is_consistent_strong = False
        print(f'avg: {avg_win_rate}, weak: {mean_counter}, strong: {mean_strong}')
        if avg_win_rate:
            if mean_counter and mean_strong:
                is_consistent_strong = (mean_strong >= avg_win_rate)
                is_consistent_weak = (mean_counter <= avg_win_rate)

            elif mean_counter:
                is_consistent_strong = True
                is_consistent_weak = (mean_counter <= avg_win_rate)
 
            elif mean_strong:
                is_consistent_strong = (mean_strong >= avg_win_rate)
                is_consistent_weak = True

            else:
                print("Not computable!!!!")
                is_consistent_strong = True
                is_consistent_weak = True
        else:
            if mean_counter and mean_strong:
                is_consistent_strong = (mean_strong > mean_counter)
                is_consistent_weak = (mean_strong > mean_counter)
                
            else:
                print("Not computable!!")
                is_consistent_strong = True
                is_consistent_weak = True
        

        if not is_consistent_weak:
            print("NOT Consistent weak")
            list_inconsistent_weak.append(df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking)])
            num_inconsistent+= 1

        if not is_consistent_strong:
            print("NOT Consistent strong")
            list_inconsistent_strong.append(df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking)])
            
            if is_consistent_weak:
                num_inconsistent+= 1

        num_iterations+=1



============================24==============================
24 - 1 - 0
Counter:     winrate  champion_vs_ID  games_played
0    44.01              86        100862
1    44.53             420         50803
2    44.85              36         28349
3    44.86              27         14508
4    45.80             154          5380
Strong:     winrate  champion_vs_ID  games_played
5    55.01              39         33167
6    54.88             157         19581
7    54.02             777         89243
8    53.73             106         33202
9    52.95              19          9495
avg: 50.2, weak: 44.81, strong: 54.117999999999995
24 - 1 - 1
Counter:        winrate  champion_vs_ID  games_played
3728    43.33             897            30
3729    43.33              79            30
3730    48.21             266            56
avg: 59.3, weak: 44.95666666666667, strong: None
24 - 1 - 2
Counter:        winrate  champion_vs_ID  games_played
3814    40.00              57            95
3815    40.

In [6]:
num_inconsistent / num_iterations * 100

3.440482169763938

3.44% inconsistent. 

### Completeness
Completeness in matchup, does every combination of champion, lane and ranking in game_stats have  5 weak against and 5 strong against in matchup?

In [7]:
#Compute matchup object completeness
round(len(matchup) / (len(df_game_stats) * 10) * 100, 2)

84.59

Matchup Object Completeness = 84.59%

### Improvement Phase for Matchup

I give priority to consistency, so the focus is to have a 100% consistency for matchup. To achieve this goal, i need to give up a little bit 
on completeness.

In [8]:
df_inconsistent_strong = pd.concat(list_inconsistent_strong)
df_inconsistent_strong

position  win_rate  pick_rate  ban_rate  pbi  games_played     grade  \
2592        17     55.06       0.33      1.39    0          1235  3.166500   
1768        43     55.35       0.47      2.29    1          1756  3.166500   
2590        15     59.10       0.27      0.37    1          1022  3.000000   
96           3     60.09       7.69      6.88   21           847  2.444333   
3077        63     52.26       0.24      0.17    0           907  4.666500   
281         50     53.72       0.06      0.78    0           646  3.000000   
2600        25     57.38       0.13      0.56    0           488  3.666500   
2551         4     55.89      18.59     10.41  -34          2045  1.888667   
2579         4     53.42      15.55      7.98  -12         57964  2.222000   
100          7     60.34       7.90      8.66   25           870  3.000000   
153         11     56.96       0.15      1.74    0           546  2.333000   
3044        30     53.96       0.42     10.10    0          1566  3.000000   
218         76     52.14       0.12      1.23    0           443  4.333000   
2595        20     57.31       0.21      1.04    1           780  3.333000   
102          9     58.64       3.47      2.09    4           382  3.111000   
1082        52     52.51       0.41      0.72   -1          1493  4.166500   
1696        10     60.13       8.88     21.31   30          1056  3.000000   
2552         5     54.67      11.87     10.28  -38          1306  2.000000   
2597        22     53.47       6.05      8.59   -4         22558  3.444333   
3034        20     55.32       0.10      2.26    0           376  2.666500   
1069        39     55.81       0.50      0.10    1          1842  3.666667   
992          5     60.72       7.38      9.78   26           942  2.000000   
1002        15     58.66       6.20      5.58    8           791  3.000000   
1001        14     59.04       6.72      4.34   11           857  2.888667   
1767        42     53.58       0.48      4.45    0          1786  3.166500   
2989         6     59.45       9.64      5.49   20           952  2.000000   
988          1     56.40      23.46     14.12  -30          2993  1.110667   
3103        21     54.84       0.08      2.02    0           764  2.333000   
996          9     58.20       7.31      7.19    5           933  2.444333   
3070        56     52.98       2.42     10.07   -3          9065  4.000000   
1691         5     57.70      11.52     11.83    2          1371  2.777667   
2586        11     56.38       0.21      2.34    0           784  2.833000   
2606        31     54.50       2.90      0.64    1         10812  3.888667   
3032        18     55.60       0.32      2.22    0          1214  2.666500   
1687         1     56.45      14.53     20.36  -19          1729  1.833000   
2577         2     52.60      22.29      5.03  -36         83112  1.444333   
2548         1     58.77      21.76     12.25   31          2394  0.888667   
2576         1     54.78      24.93     13.84   19         92961  0.888667   
2616         1     52.25      25.45     13.84   13        261635  1.222000   
2585        10     54.68      13.28      5.30    8         49496  2.666667   
2553         6     58.22      10.94      0.51    8          1204  2.222000   
2581         6     54.57      12.97      0.76    6         48342  2.333333   
2985         2     57.84      14.08     12.67    5          1390  1.222000   
2550         3     59.19       8.75     30.69   21           963  1.777667   
2588        13     52.68       9.18      4.67  -14         34243  3.000000   
2593        18     54.62       0.24     10.78    0           877  3.166500   
2991         8     59.72       9.33      3.11   21           921  2.444333   

      lane_ID  ranking_ID  champion_ID  
2592        4           2           69  
1768        3           2           75  
2590        4           2          223  
96          1           1           92  
3077        5           2           98  
281         1  

Remove inconsistent strong

In [9]:
for index, row_inconsistent_strong in df_inconsistent_strong.iterrows():
    lane_ID = row_inconsistent_strong['lane_ID']
    ranking_ID = row_inconsistent_strong['ranking_ID']
    champion_ID = row_inconsistent_strong['champion_ID']

    type = 'strong'
    print(f"======= Rimuovo {lane_ID} - {ranking_ID} - {champion_ID}")
    matchup = matchup.loc[~((matchup['lane_ID'] == lane_ID) & 
                          (matchup['ranking_ID'] == ranking_ID) &
                          (matchup['champion_ID'] == champion_ID) &
                          (matchup['type'] == type))]
    




======= Rimuovo 4.0 - 2.0 - 69.0
======= Rimuovo 3.0 - 2.0 - 75.0
======= Rimuovo 4.0 - 2.0 - 223.0
======= Rimuovo 1.0 - 1.0 - 92.0
======= Rimuovo 5.0 - 2.0 - 98.0
======= Rimuovo 1.0 - 3.0 - 136.0
======= Rimuovo 4.0 - 2.0 - 136.0
======= Rimuovo 4.0 - 1.0 - 110.0
======= Rimuovo 4.0 - 2.0 - 110.0
======= Rimuovo 1.0 - 1.0 - 897.0
======= Rimuovo 1.0 - 2.0 - 34.0
======= Rimuovo 5.0 - 2.0 - 7.0
======= Rimuovo 1.0 - 2.0 - 112.0
======= Rimuovo 4.0 - 2.0 - 74.0
======= Rimuovo 1.0 - 1.0 - 79.0
======= Rimuovo 2.0 - 2.0 - 106.0
======= Rimuovo 3.0 - 1.0 - 777.0
======= Rimuovo 4.0 - 1.0 - 429.0
======= Rimuovo 4.0 - 2.0 - 429.0
======= Rimuovo 5.0 - 2.0 - 427.0
======= Rimuovo 2.0 - 2.0 - 72.0
======= Rimuovo 2.0 - 1.0 - 163.0
======= Rimuovo 2.0 - 1.0 - 56.0
======= Rimuovo 2.0 - 1.0 - 63.0
======= Rimuovo 3.0 - 2.0 - 63.0
======= Rimuovo 5.0 - 1.0 - 526.0


======= Rimuovo 2.0 - 1.0 - 64.0
======= Rimuovo 5.0 - 3.0 - 60.0
======= Rimuovo 2.0 - 1.0 - 76.0
======= Rimuovo 5.0 - 2.0 - 25.0
======= Rimuovo 3.0 - 1.0 - 134.0
======= Rimuovo 4.0 - 2.0 - 99.0
======= Rimuovo 4.0 - 2.0 - 18.0
======= Rimuovo 5.0 - 2.0 - 142.0
======= Rimuovo 3.0 - 1.0 - 61.0
======= Rimuovo 4.0 - 2.0 - 145.0
======= Rimuovo 4.0 - 1.0 - 81.0
======= Rimuovo 4.0 - 2.0 - 81.0
======= Rimuovo 4.0 - 3.0 - 81.0
======= Rimuovo 4.0 - 2.0 - 236.0
======= Rimuovo 4.0 - 1.0 - 202.0
======= Rimuovo 4.0 - 2.0 - 202.0
======= Rimuovo 5.0 - 1.0 - 22.0
======= Rimuovo 4.0 - 1.0 - 119.0
======= Rimuovo 4.0 - 2.0 - 498.0
======= Rimuovo 4.0 - 2.0 - 235.0
======= Rimuovo 5.0 - 1.0 - 888.0


In [10]:
df_inconsistent_weak = pd.concat(list_inconsistent_weak)
df_inconsistent_weak

position  win_rate  pick_rate  ban_rate  pbi  games_played     grade  \
861         57     41.63       0.16      1.19    0          1165  3.166500   
2871        16     43.66       8.34      9.39   -5         58203  2.444333   
2883        28     43.48       0.24      1.87    0          1686  3.000000   
2417        20     48.34       0.14      1.65    1           991  2.166500   
811          7     46.43      10.39      6.61   25         76672  1.777667   
...        ...       ...        ...       ...  ...           ...       ...   
3585        34     43.75       9.52      5.24   -4         75867  2.555333   
823         19     42.90       0.25      5.24    0          1837  2.166500   
2867        12     44.12      20.05     16.21   -1        139994  2.111000   
2901        46     42.68       3.47      0.93   -5         24194  4.111000   
2897        42     41.23       2.07      0.58   -6         14444  3.888667   

      lane_ID  ranking_ID  champion_ID  
861         1           9           69  
2871        4           9           67  
2883        4           9          133  
2417        3           9            6  
811         1           9           86  
...       ...         ...          ...  
3585        5           9          235  
823         1           9          235  
2867        4           9           51  
2901        4           9           15  
2897        4           9          221  

[90 rows x 10 columns]

Rimuovo inconsistent weak in matchup

In [11]:
for index, row_inconsistent_weak in df_inconsistent_weak.iterrows():
    lane_ID = row_inconsistent_weak['lane_ID']
    ranking_ID = row_inconsistent_weak['ranking_ID']
    champion_ID = row_inconsistent_weak['champion_ID']

    type = 'counter'
    print(f"======= Rimuovo {lane_ID} - {ranking_ID} - {champion_ID}")
    matchup = matchup.loc[~((matchup['lane_ID'] == lane_ID) & 
                          (matchup['ranking_ID'] == ranking_ID) &
                          (matchup['champion_ID'] == champion_ID) &
                          (matchup['type'] == type))]

======= Rimuovo 1.0 - 9.0 - 69.0
======= Rimuovo 4.0 - 9.0 - 67.0
======= Rimuovo 4.0 - 9.0 - 133.0
======= Rimuovo 3.0 - 9.0 - 6.0
======= Rimuovo 1.0 - 9.0 - 86.0
======= Rimuovo 4.0 - 9.0 - 50.0
======= Rimuovo 3.0 - 9.0 - 517.0
======= Rimuovo 1.0 - 9.0 - 57.0
======= Rimuovo 1.0 - 9.0 - 48.0
======= Rimuovo 3.0 - 9.0 - 23.0
======= Rimuovo 2.0 - 9.0 - 36.0
======= Rimuovo 2.0 - 9.0 - 518.0
======= Rimuovo 1.0 - 9.0 - 238.0
======= Rimuovo 1.0 - 9.0 - 266.0
======= Rimuovo 5.0 - 5.0 - 136.0
======= Rimuovo 3.0 - 9.0 - 110.0
======= Rimuovo 4.0 - 9.0 - 110.0
======= Rimuovo 5.0 - 9.0 - 110.0
======= Rimuovo 1.0 - 9.0 - 122.0
======= Rimuovo 2.0 - 9.0 - 122.0
======= Rimuovo 3.0 - 9.0 - 897.0
======= Rimuovo 1.0 - 7.0 - 246.0
======= Rimuovo 2.0 - 9.0 - 246.0
======= Rimuovo 1.0 - 9.0 - 950.0
======= Rimuovo 2.0 - 9.0 - 950.0
======= Rimuovo 3.0 - 9.0 - 112.0
======= Rimuovo 3.0 - 9.0 - 58.0
======= Rimuovo 5.0 - 9.0 - 30.0
======= Rimuovo 2.0 - 9.0 - 887.0
======= Rimuovo 3.0 - 9.0 

Calcolo di nuovo consistency e completeness

In [12]:
num_iterations = 0
num_inconsistent = 0
list_inconsistent_weak = []
list_inconsistent_strong = []
for champion in champion_ID_list:
    print(f'============================{champion}==============================')
    filter_champion = (matchup['champion_ID'] == champion)

    lanes = list(matchup[filter_champion]['lane_ID'].unique())
    rankings = list(matchup[filter_champion]['ranking_ID'].unique())

    for lane, ranking in product(lanes, rankings):
        print(f'{champion} - {lane} - {ranking}')
        is_computable = False
        filter_2 = (matchup['lane_ID'] == lane) & (matchup['ranking_ID'] == ranking)

        subset = matchup[filter_champion & filter_2]
        mean_counter = None
        mean_strong = None

        if len(subset[subset['type'] == 'counter']) > 0:
            print('Counter: ', subset[subset['type'] == 'counter'][['winrate', 'champion_vs_ID', 'games_played']])
            mean_counter = subset[subset['type'] == 'counter']['winrate'].mean()

        if len(subset[subset['type'] == 'strong']) > 0:
            print('Strong: ', subset[subset['type'] == 'strong'][['winrate', 'champion_vs_ID', 'games_played']])
            mean_strong =  subset[subset['type'] == 'strong']['winrate'].mean()

        avg_win_rate = (df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking), 'win_rate'])
        
        if len(avg_win_rate) > 0:
            if len(avg_win_rate) == 1:
                avg_win_rate = float(avg_win_rate.iloc[0])
            else:
                raise ValueError("Qui valori multipli. problema")
        else:
            avg_win_rate = None

        is_consistent_weak = False 
        is_consistent_strong = False
        print(f'avg: {avg_win_rate}, weak: {mean_counter}, strong: {mean_strong}')
        if avg_win_rate:
            if mean_counter and mean_strong:
                is_consistent_strong = (mean_strong >= avg_win_rate)
                is_consistent_weak = (mean_counter <= avg_win_rate)

            elif mean_counter:
                is_consistent_strong = True
                is_consistent_weak = (mean_counter <= avg_win_rate)
 
            elif mean_strong:
                is_consistent_strong = (mean_strong >= avg_win_rate)
                is_consistent_weak = True

            else:
                print("Not computable!!!!")
                is_consistent_strong = True
                is_consistent_weak = True
        else:
            if mean_counter and mean_strong:
                is_consistent_strong = (mean_strong > mean_counter)
                is_consistent_weak = (mean_strong > mean_counter)
                
            else:
                print("Not computable!!")
                is_consistent_strong = True
                is_consistent_weak = True
        

        if not is_consistent_weak:
            print("NOT Consistent weak")
            list_inconsistent_weak.append(df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking)])
            num_inconsistent+= 1

        if not is_consistent_strong:
            print("NOT Consistent strong")
            list_inconsistent_strong.append(df_game_stats.loc[(df_game_stats['champion_ID'] == champion) & 
                                     (df_game_stats['lane_ID'] == lane) & 
                                     (df_game_stats['ranking_ID'] == ranking)])
            
            if is_consistent_weak:
                num_inconsistent+= 1

        num_iterations+=1

============================24==============================
24 - 1 - 0
Counter:     winrate  champion_vs_ID  games_played
0    44.01              86        100862
1    44.53             420         50803
2    44.85              36         28349
3    44.86              27         14508
4    45.80             154          5380
Strong:     winrate  champion_vs_ID  games_played
5    55.01              39         33167
6    54.88             157         19581
7    54.02             777         89243
8    53.73             106         33202
9    52.95              19          9495
avg: 50.2, weak: 44.81, strong: 54.117999999999995
24 - 1 - 1
Counter:        winrate  champion_vs_ID  games_played
3728    43.33             897            30
3729    43.33              79            30
3730    48.21             266            56
avg: 59.3, weak: 44.95666666666667, strong: None
24 - 1 - 2
Counter:        winrate  champion_vs_ID  games_played
3814    40.00              57            95
3815    40.

avg: 50.38, weak: 44.556, strong: 53.968
24 - 1 - 6
Counter:         winrate  champion_vs_ID  games_played
16909    43.35              86          6782
16910    43.59             420          3308
16911    43.68             154           364
16912    44.07              27           894
16913    44.26               8           479
Strong:         winrate  champion_vs_ID  games_played
16914    55.98             157          1213
16915    54.89              39          2106
16916    54.80             777          5695
16917    53.61             164          2076
16918    53.59              74           390
avg: 50.0, weak: 43.79, strong: 54.574
24 - 1 - 7
Counter:         winrate  champion_vs_ID  games_played
20667    41.75              27           836
20668    42.33              36          2015
20669    42.96              86          6629
20670    44.81              54          3401
20671    45.50              75          3303
Strong:         winrate  champion_vs_ID  games_played
20672

In [13]:
num_inconsistent / num_iterations

0.0

In [14]:
len(matchup) / (len(df_game_stats) * 10) * 100

83.29595185995625

New Matchup Consistency = 100%

New Matchup Completeness = 83.3%

In [15]:
# Salvo il nuovo matchup
matchup.to_excel('datasets_cleaned/matchup.xlsx', index = False)

Computing table completeness for tables containing basic Champion information

In [16]:
df_champion_base_info = pd.read_excel('datasets_cleaned/champion_base_info.xlsx')
df_champion_base_stats = pd.read_excel('datasets_cleaned/champion_base_stats.xlsx')
df_champion_name = pd.read_excel('datasets_cleaned/champion_name.xlsx')

In [17]:
(1 - df_champion_base_info.isnull().mean().mean()) * 100

99.47289156626506

Table Completeness Champion Base Info: 99.5%

Investigating rows with NaN values

In [18]:
df_champion_base_info[df_champion_base_info.isnull().any(axis=1)]

champion_ID                    title  \
13           200  the Empress of the Void   
26            36       the Madman of Zaun   
36            86     The Might of Demacia   
58            55       the Sinister Blade   
108           92                the Exile   
147          234          The Ruined King   
159          154        the Secret Weapon   

                                                 blurb partype  attack  \
13   A nightmarish empress created from the raw mat...     NaN       4   
26   Utterly mad, tragically homicidal, and horrify...     NaN       5   
36   A proud and noble warrior, Garen fights as one...     NaN       7   
58   Decisive in judgment and lethal in combat, Kat...     NaN       4   
108  Once a swordmaster in the warhosts of Noxus, R...     NaN       8   
147  Once ruler of a long-lost kingdom, Viego peris...     NaN       6   
159  Zac is the product of a toxic spill that ran t...     NaN       3   

     defense  magic  difficulty  
13         2      7          10  
26         7      6           5  
36         7      1           5  
58         3      9           8  
108        5      1           8  
147        4      2           5  
159        7      7           8

These are champions that don't use any type of resource (Mana, Blood, Energy, Fury). Instead of NaN, I use 'Resourceless'.

In [19]:
df_champion_base_info['partype'].fillna('Resourceless', inplace=True)


In [20]:
(1 - df_champion_base_info.isnull().mean().mean()) * 100

100.0

In [21]:
df_champion_base_info.to_excel('datasets_cleaned/champion_base_info.xlsx', index = False)

In [22]:
(1 - df_champion_base_stats.isnull().mean().mean()) * 100

100.0

In [23]:
(1 - df_champion_name.isnull().mean().mean()) * 100

100.0

Table Completeness:
- champion_base_info = 100%
- champion_base_stats = 100%
- champion_name = 100%